In [1]:
import numpy as np
import datetime

In [2]:
import pandas as pd

In [185]:
# read in raw data
AVG_TIME20 = pd.read_csv("C:/Users/Administrator/PycharmProjects/Traffic/Data/training_20min_avg_travel_time-Copy1.csv")
AVG_TIME20['START_TIME'] = AVG_TIME20['time_window'].apply(lambda x :(x.split(','))[0][1:])
AVG_TIME20.drop(['time_window'],axis=1,inplace=True)

In [186]:
AVG_TIME20['START_TIME'] = pd.DataFrame(AVG_TIME20['START_TIME'])

In [187]:
MIN20_N = 24*3*91
end_date = datetime.datetime.strptime('2016-10-17 23:40:00','%Y-%m-%d %H:%M:%S')
date_list = [str((end_date - datetime.timedelta(minutes=20*x))) for x in range(MIN20_N)]
date_list.reverse()
date_list_df = pd.DataFrame(date_list)
date_list_df = date_list_df.rename(columns={0:'START_TIME'})
AVG_TIME20_FULL = pd.DataFrame(columns={'START_TIME','intersection_id','tollgate_id','avg_travel_time'})
for key,values in AVG_TIME20.groupby(['intersection_id','tollgate_id']):
    values = pd.merge(date_list_df,values,on='START_TIME',how='left')
    values['intersection_id'].fillna(method='backfill',inplace=True)
    values['tollgate_id'].fillna(method='backfill',inplace=True)
    AVG_TIME20_FULL = pd.concat([AVG_TIME20_FULL,values],axis=0)

In [190]:
AVG_TIME20_TAB = pd.pivot_table(AVG_TIME20_FULL, values=['avg_travel_time'], index=['intersection_id','tollgate_id'],columns=['START_TIME'], aggfunc=np.sum)   

In [192]:
AVG_TIME20_TAB.columns = [str(start_date + datetime.timedelta(minutes=20*x)) for x in range( AVG_TIME20_TAB.shape[1])]

In [194]:
AVG_TIME20_TAB

2016-07-19 00:00:00  2016-07-19 00:20:00  \
intersection_id tollgate_id                                             
A               2.0                          NaN                58.05   
                3.0                          NaN                  NaN   
B               1.0                          NaN                79.76   
                3.0                        70.85               148.79   
C               1.0                          NaN                  NaN   
                3.0                          NaN                  NaN   

                             2016-07-19 00:40:00  2016-07-19 01:00:00  \
intersection_id tollgate_id                                             
A               2.0                          NaN                  NaN   
                3.0                          NaN                  NaN   
B               1.0                       137.98                  NaN   
                3.0                          NaN                  NaN   
C               1.0                          NaN                  NaN   
                3.0                       113.54                  NaN   

                             2016-07-19 01:20:00  2016-07-19 01:40:00  \
intersection_id tollgate_id                                             
A               2.0                        56.87                77.74   
                3.0                        94.57                  NaN   
B               1.0                       176.70                  NaN   
                3.0                          NaN                93.72   
C               1.0                       214.87               160.63   
                3.0                          NaN                  NaN   

                             2016-07-19 02:00:00  2016-07-19 02:20:00  \
intersection_id tollgate_id                                             
A               2.0                          NaN                42.64   
                3.0                          NaN                77.61   
B               1.0                          NaN                  NaN   
                3.0                        67.81                  NaN   
C               1.0                          NaN                  NaN   
                3.0                          NaN                  NaN   

                             2016-07-19 02:40:00  2016-07-19 03:00:00  \
intersection_id tollgate_id                                             
A               2.0                        40.17                  NaN   
                3.0                          NaN                93.09   
B               1.0                          NaN                  NaN   
                3.0                       167.55                  NaN   
C               1.0                          NaN                  NaN   
                3.0                          NaN                  NaN   

                             2016-07-19 03:20:00  2016-07-19 03:40:00  \
intersection_id tollgate_id                                             
A               2.0                        41.92                39.43   
                3.0                          NaN                  NaN   
B               1.0                          NaN                  NaN   
                3.0                          NaN                98.49   
C               1.0                          NaN                  NaN   
                3.0                          NaN                  NaN   

                             2016-07-19 04:00:00  2016-07-19 04:20:00  \
intersection_id tollgate_id                                             
A               2.0                        48.13                62.11   
                3.0                          NaN                  NaN   
B               1.0                          NaN                94.06   
                3.0                        96.67                53.15   
C               1.0                          NaN                  NaN   
        

In [195]:
# train data time
TRN_N = 6
TST_N = 6   
MIN20_N = 24*3*91

In [196]:
# zip 用法a=[1,2,3] b=[7,7,7,7,7,7] list(zip(a,b)) [(1, 7), (2, 7), (3, 7)]
TRAIN = pd.DataFrame()
train_date_zip = list(zip(date_list[0:MIN20_N-(TRN_N+TST_N)+1],date_list[TRN_N-1:MIN20_N-TST_N+1],date_list[TRN_N:MIN20_N-TST_N+2],date_list[TRN_N+TST_N-1:MIN20_N]))
train_date_zip_df = pd.DataFrame(train_date_zip)
train_date_zip_df.columns = ['TRN_STA','TRN_END','TST_STA','TST_END']

In [198]:
train_date_zip_df.head()

TRN_STA              TRN_END              TST_STA  \
0  2016-07-19 00:00:00  2016-07-19 01:40:00  2016-07-19 02:00:00   
1  2016-07-19 00:20:00  2016-07-19 02:00:00  2016-07-19 02:20:00   
2  2016-07-19 00:40:00  2016-07-19 02:20:00  2016-07-19 02:40:00   
3  2016-07-19 01:00:00  2016-07-19 02:40:00  2016-07-19 03:00:00   
4  2016-07-19 01:20:00  2016-07-19 03:00:00  2016-07-19 03:20:00   

               TST_END  
0  2016-07-19 03:40:00  
1  2016-07-19 04:00:00  
2  2016-07-19 04:20:00  
3  2016-07-19 04:40:00  
4  2016-07-19 05:00:00

In [202]:
for TRN_STA,TRN_END,TST_STA,TST_END in train_date_zip:
    TRAIN_temp = AVG_TIME20_TAB.loc[:,TRN_STA:TST_END] 
    TRAIN_temp.columns = np.arange(TRAIN_temp.shape[1])
    TRAIN_temp.reset_index(level=0, inplace=True)
    TRAIN_temp.loc[:,'TRN_STA']  = str(TRN_STA)
    TRAIN_temp.loc[:,'TRN_END'] = str(TRN_END)    
    TRAIN_temp.loc[:,'TST_STA']  = str(TST_STA)
    TRAIN_temp.loc[:,'TST_END'] = str(TST_END)    
    TRAIN = pd.concat( [TRAIN,TRAIN_temp],) 

f:\python35\lib\site-packages\pandas\core\indexing.py:297: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self.obj[key] = _infer_fill_value(value)
f:\python35\lib\site-packages\pandas\core\indexing.py:477: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self.obj[item] = s


In [206]:
TRAIN = TRAIN.reset_index()

In [204]:
TRAIN_TRN_C =  list(map(lambda x:'SA'+ str(x).zfill(2), np.arange(TRN_N)))
TRAIN_TST_C =  list(map(lambda x:'SB'+ str(x).zfill(2), np.arange(TST_N)))

In [208]:
TRAIN.columns = ['TOLLGATE_ID','INTERSECTION_ID']  + TRAIN_TRN_C + TRAIN_TST_C  + ['TRN_STA','TRN_END','TST_STA','TST_END']

In [568]:
#### #### #### #### #### #### #### #### #### #### #### #### #### #### #### #### #### #### #### #### #### 

In [213]:
TRAIN_OK = TRAIN[TRAIN.loc[:,TRAIN_TST_C].isnull().sum(axis = 1)==0]

In [216]:
# IF TRAIN CONTAIN NAN --> DEL
TRAIN_OK = TRAIN_OK[TRAIN_OK.loc[:,TRAIN_TRN_C].isnull().sum(axis = 1)<=(TRN_N-6)]

In [217]:
TRAIN_OK

TOLLGATE_ID INTERSECTION_ID    SA00    SA01    SA02    SA03    SA04  \
60             2.0               A   41.92   39.43   48.13   62.11   46.12   
66             2.0               A   39.43   48.13   62.11   46.12   49.56   
72             2.0               A   48.13   62.11   46.12   49.56   54.84   
78             2.0               A   62.11   46.12   49.56   54.84   58.08   
84             2.0               A   46.12   49.56   54.84   58.08   46.36   
90             2.0               A   49.56   54.84   58.08   46.36   48.59   
96             2.0               A   54.84   58.08   46.36   48.59   66.64   
102            2.0               A   58.08   46.36   48.59   66.64   64.68   
108            2.0               A   46.36   48.59   66.64   64.68   85.68   
109            3.0               A  124.66   89.85  180.02  101.39  124.29   
111            3.0               B  145.94  127.35   97.20  118.43   82.63   
114            2.0               A   48.59   66.64   64.68   85.68   58.97   
115            3.0               A   89.85  180.02  101.39  124.29  155.49   
117            3.0               B  127.35   97.20  118.43   82.63  110.50   
120            2.0               A   66.64   64.68   85.68   58.97   81.60   
121            3.0               A  180.02  101.39  124.29  155.49  137.38   
123            3.0               B   97.20  118.43   82.63  110.50  125.76   
126            2.0               A   64.68   85.68   58.97   81.60   80.21   
127            3.0               A  101.39  124.29  155.49  137.38  165.48   
129            3.0               B  118.43   82.63  110.50  125.76  141.33   
132            2.0               A   85.68   58.97   81.60   80.21   63.45   
133            3.0               A  124.29  155.49  137.38  165.48  136.68   
135            3.0               B   82.63  110.50  125.76  141.33  176.08   
138            2.0               A   58.97   81.60   80.21   63.45   78.05   
139            3.0               A  155.49  137.38  165.48  136.68  192.68   
141            3.0               B  110.50  125.76  141.33  176.08  165.29   
144            2.0               A   81.60   80.21   63.45   78.05   69.04   
145            3.0               A  137.38  165.48  136.68  192.68  159.78   
147            3.0               B  125.76  141.33  176.08  165.29  127.38   
150            2.0               A   80.21   63.45   78.05   69.04   69.66   
...            ...             ...     ...     ...     ...     ...     ...   
39156          2.0               A   90.64   71.70   53.86   69.77   61.90   
39157          3.0               A  117.88  131.03  109.92  111.73  118.20   
39162          2.0               A   71.70   53.86   69.77   61.90   76.76   
39163          3.0               A  131.03  109.92  111.73  118.20  125.57   
39168          2.0               A   53.86   69.77   61.90   76.76   58.04   
39169          3.0               A  109.92  111.73  118.20  125.57  152.19   
39174          2.0               A   69.77   61.90   76.76   58.04   53.69   
39175          3.0               A  111.73  118.20  125.57  152.19  125.55   
39180          2.0               A   61.90   76.76   58.04   53.69   65.40   
39181          3.0               A  118.20  125.57  152.19  125.55  158.01   
39186          2.0               A   76.76   58.04   53.69   65.40   48.66   
39187          3.0               A  125.57  152.19  125.55  158.01  115.05   
39192          2.0               A   58.04   53.69   65.40   48.66   60.41   
39193          3.0               A  152.19  125.55  158.01  115.05  116.37   
39198          2.0               A   53.69   65.40   48.66   60.41   85.12   
39199          3.0               A  125.55  158.01  115.05  116.37  107.77   
39204          2.0               A   65.40   48.66   60.41   85.12   67.14   
39205          3.0               A  158.01  115.05  116.37  107.77  131.23   
39210          2.0               A   48.66   60.41   85.12   67.14   65.93   
39211          3.0           

In [569]:
TRAIN_OK.to_csv("TRAIN_OK.csv",index=None,encoding='utf-8')

In [ ]:
# ###  TEST DATA GENERATE

In [457]:
TEST = pd.read_csv("C:/Users/Administrator/PycharmProjects/Traffic/Data/test1_20min_avg_travel_time.csv")

In [458]:
TEST['START_TIME'] = TEST['time_window'].apply(lambda x :(x.split(','))[0][1:])
TEST.drop(['time_window'],axis=1,inplace=True)

In [459]:
DAY_N = 7
MIN20_N = 24*3*DAY_N
end_date = datetime.datetime.strptime('2016-10-24 23:40:00','%Y-%m-%d %H:%M:%S')
date_list = [str((end_date- datetime.timedelta(minutes=20*x))) for x in range(MIN20_N)]
date_list.reverse()

In [460]:
date_list_datetime = pd.to_datetime(date_list)

In [461]:
morning_start = datetime.datetime.strptime('2016-10-18 06:00:00','%Y-%m-%d %H:%M:%S')
morning_end = datetime.datetime.strptime('2016-10-18 07:40:00','%Y-%m-%d %H:%M:%S')
afternoon_start = datetime.datetime.strptime('2016-10-18 15:00:00','%Y-%m-%d %H:%M:%S')
afternoon_end = datetime.datetime.strptime('2016-10-18 16:40:00','%Y-%m-%d %H:%M:%S')

In [462]:
def GetDateList(date_list,date_list_datetime,morning_start,morning_end):
    temp_index = date_list_datetime.slice_locs(morning_start,morning_end)
    return date_list[temp_index[0]:temp_index[1]]

In [463]:
def GetDate(date_list,date_list_datetime,morning_start):
    temp_index = date_list_datetime.slice_locs(morning_start)
    return date_list[temp_index[0]]

In [464]:
test_date_zip_df = pd.DataFrame(columns={'START_TIME'})

In [465]:
for x in range(DAY_N):
    test_date_list_A_temp =pd.DataFrame(GetDateList(date_list,date_list_datetime,afternoon_start + datetime.timedelta(days=x),afternoon_end + datetime.timedelta(days=x)),columns={'START_TIME'})   
    test_date_list_M_temp =pd.DataFrame(GetDateList(date_list,date_list_datetime,morning_start + datetime.timedelta(days=x),morning_end + datetime.timedelta(days=x)),columns={'START_TIME'})
    test_date_zip_df = pd.concat([test_date_zip_df,test_date_list_M_temp],axis=0)
    test_date_zip_df = pd.concat([test_date_zip_df,test_date_list_A_temp],axis=0)

In [538]:
test_date_list = []
for x in range(DAY_N):
    test_date_list_M_start_temp =GetDate(date_list,date_list_datetime,morning_start + datetime.timedelta(days=x))  
    test_date_list_M_end_temp =GetDate(date_list,date_list_datetime,morning_end + datetime.timedelta(days=x)) 
    
    test_date_list_A_start_temp =GetDate(date_list,date_list_datetime,afternoon_start + datetime.timedelta(days=x))  
    test_date_list_A_end_temp =GetDate(date_list,date_list_datetime,afternoon_end + datetime.timedelta(days=x)) 
    test_date_list.append([test_date_list_M_start_temp,test_date_list_M_end_temp,test_date_list_A_start_temp,test_date_list_A_end_temp])   

In [466]:
test_date_zip_df = test_date_zip_df.reset_index(level=0,drop=True)

In [467]:
TEST

intersection_id  tollgate_id  avg_travel_time           START_TIME
0                 B            3            54.75  2016-10-18 06:00:00
1                 B            3           121.02  2016-10-18 06:20:00
2                 B            3            94.04  2016-10-18 06:40:00
3                 B            3           120.60  2016-10-18 07:00:00
4                 B            3            73.40  2016-10-18 07:20:00
5                 B            3            89.91  2016-10-18 07:40:00
6                 B            3           135.06  2016-10-18 15:00:00
7                 B            3            61.22  2016-10-18 15:20:00
8                 B            3           132.87  2016-10-18 15:40:00
9                 B            3           111.90  2016-10-18 16:00:00
10                B            3            84.37  2016-10-18 16:20:00
11                B            3            85.17  2016-10-18 16:40:00
12                B            3           102.83  2016-10-19 06:00:00
13                B            3           106.34  2016-10-19 06:20:00
14                B            3           141.43  2016-10-19 07:00:00
15                B            3            73.72  2016-10-19 07:20:00
16                B            3            80.27  2016-10-19 07:40:00
17                B            3            82.13  2016-10-19 15:00:00
18                B            3           128.95  2016-10-19 15:20:00
19                B            3            84.24  2016-10-19 15:40:00
20                B            3           115.72  2016-10-19 16:00:00
21                B            3           141.25  2016-10-19 16:20:00
22                B            3           102.53  2016-10-19 16:40:00
23                B            3           126.27  2016-10-20 06:00:00
24                B            3            84.63  2016-10-20 06:20:00
25                B            3           110.79  2016-10-20 06:40:00
26                B            3            66.86  2016-10-20 07:20:00
27                B            3           107.81  2016-10-20 07:40:00
28                B            3           122.19  2016-10-20 15:00:00
29                B            3            77.16  2016-10-20 15:20:00
..              ...          ...              ...                  ...
418               C            1           165.57  2016-10-22 06:40:00
419               C            1           131.62  2016-10-22 07:20:00
420               C            1           187.74  2016-10-22 07:40:00
421               C            1           184.88  2016-10-22 15:20:00
422               C            1           245.56  2016-10-22 15:40:00
423               C            1           222.29  2016-10-22 16:00:00
424               C            1           178.02  2016-10-22 16:20:00
425               C            1           242.56  2016-10-22 16:40:00
426               C            1           207.94  2016-10-23 06:00:00
427               C            1           219.97  2016-10-23 06:40:00
428               C            1           124.00  2016-10-23 07:00:00
429               C            1           127.91  2016-10-23 07:20:00
430               C            1           148.54  2016-10-23 07:40:00
431               C            1           160.53  2016-10-23 15:00:00
432               C            1           206.22  2016-10-23 15:20:00
433               C            1           195.08  2016-10-23 15:40:00
434               C            1           176.23  2016-10-23 16:00:00
435               C            1           196.48  2016-10-23 16:20:00
436               C            1           352.44  2016-10-23 16:40:00
437               C            1           171.65  2016-10-24 06:00:00
438               C            1           138.84  2016-10-24 06:40:00
439               C            1           176.69  2016-10-24 07:00:00
440               C            1           235.80  2016-10-24 07:20:00
441               C            1           272.82  2016-10-24 07:40:00
442               C         

In [468]:
TEST_FULL = pd.DataFrame(columns={'START_TIME','intersection_id','tollgate_id','avg_travel_time'})
for key,values in TEST.groupby(['intersection_id','tollgate_id']):
    values = pd.merge(test_date_zip_df,values,on='START_TIME',how='left')
    values['intersection_id'].fillna(method='backfill',inplace=True)
    values['tollgate_id'].fillna(method='backfill',inplace=True)
    TEST_FULL = pd.concat([TEST_FULL,values],axis=0)

In [470]:
TEST_FULL = TEST_FULL.reset_index(level=0,drop=True)

In [471]:
TEST_FULL_TAB = pd.pivot_table(TEST_FULL, values=['avg_travel_time'], index=['intersection_id','tollgate_id'],columns=['START_TIME'], aggfunc=np.sum)

In [474]:
TEST_FULL_TAB.columns = test_date_zip_df.START_TIME

In [475]:
TEST_FULL_TAB

START_TIME                   2016-10-18 06:00:00  2016-10-18 06:20:00  \
intersection_id tollgate_id                                             
A               2.0                        41.10                43.68   
                3.0                        69.48               142.01   
B               1.0                        57.82                48.68   
                3.0                        54.75               121.02   
C               1.0                       145.35               136.22   
                3.0                       139.53                  NaN   

START_TIME                   2016-10-18 06:40:00  2016-10-18 07:00:00  \
intersection_id tollgate_id                                             
A               2.0                        68.02                52.61   
                3.0                       233.68               143.65   
B               1.0                       112.52                97.32   
                3.0                        94.04               120.60   
C               1.0                       147.82               180.98   
                3.0                       104.42               182.06   

START_TIME                   2016-10-18 07:20:00  2016-10-18 07:40:00  \
intersection_id tollgate_id                                             
A               2.0                        56.17                63.60   
                3.0                       151.51               207.71   
B               1.0                          NaN               129.44   
                3.0                        73.40                89.91   
C               1.0                       136.51               311.04   
                3.0                          NaN                  NaN   

START_TIME                   2016-10-18 15:00:00  2016-10-18 15:20:00  \
intersection_id tollgate_id                                             
A               2.0                        99.96                88.36   
                3.0                       133.05               121.57   
B               1.0                       142.75               108.19   
                3.0                       135.06                61.22   
C               1.0                       168.90               218.69   
                3.0                       164.61               146.60   

START_TIME                   2016-10-18 15:40:00  2016-10-18 16:00:00  \
intersection_id tollgate_id                                             
A               2.0                        74.89                63.30   
                3.0                       147.37               117.07   
B               1.0                        90.01               101.62   
                3.0                       132.87               111.90   
C               1.0                       178.16               158.96   
                3.0                       174.84               171.98   

START_TIME                   2016-10-18 16:20:00  2016-10-18 16:40:00  \
intersection_id tollgate_id                                             
A               2.0                        71.36                99.26   
                3.0                       134.27               139.10   
B               1.0                       150.39                  NaN   
                3.0                        84.37                85.17   
C               1.0                       181.91               196.36   
                3.0                       219.82               176.00   

START_TIME                   2016-10-19 06:00:00  2016-10-19 06:20:00  \
intersection_id tollgate_id                                             
A               2.0                        40.01                57.01   
                3.0                        89.51               161.63   
B               1.0                       111.04                  NaN   
                3.0                       102.83               106.34   
C               1.0                          NaN    

In [535]:
TEST_FULL_TAB_FILL = TEST_FULL_TAB.fillna(method='ffill',axis=1)

In [536]:
TEST_FULL_TAB_FILL

START_TIME                   2016-10-18 06:00:00  2016-10-18 06:20:00  \
intersection_id tollgate_id                                             
A               2.0                        41.10                43.68   
                3.0                        69.48               142.01   
B               1.0                        57.82                48.68   
                3.0                        54.75               121.02   
C               1.0                       145.35               136.22   
                3.0                       139.53               139.53   

START_TIME                   2016-10-18 06:40:00  2016-10-18 07:00:00  \
intersection_id tollgate_id                                             
A               2.0                        68.02                52.61   
                3.0                       233.68               143.65   
B               1.0                       112.52                97.32   
                3.0                        94.04               120.60   
C               1.0                       147.82               180.98   
                3.0                       104.42               182.06   

START_TIME                   2016-10-18 07:20:00  2016-10-18 07:40:00  \
intersection_id tollgate_id                                             
A               2.0                        56.17                63.60   
                3.0                       151.51               207.71   
B               1.0                        97.32               129.44   
                3.0                        73.40                89.91   
C               1.0                       136.51               311.04   
                3.0                       182.06               182.06   

START_TIME                   2016-10-18 15:00:00  2016-10-18 15:20:00  \
intersection_id tollgate_id                                             
A               2.0                        99.96                88.36   
                3.0                       133.05               121.57   
B               1.0                       142.75               108.19   
                3.0                       135.06                61.22   
C               1.0                       168.90               218.69   
                3.0                       164.61               146.60   

START_TIME                   2016-10-18 15:40:00  2016-10-18 16:00:00  \
intersection_id tollgate_id                                             
A               2.0                        74.89                63.30   
                3.0                       147.37               117.07   
B               1.0                        90.01               101.62   
                3.0                       132.87               111.90   
C               1.0                       178.16               158.96   
                3.0                       174.84               171.98   

START_TIME                   2016-10-18 16:20:00  2016-10-18 16:40:00  \
intersection_id tollgate_id                                             
A               2.0                        71.36                99.26   
                3.0                       134.27               139.10   
B               1.0                       150.39               150.39   
                3.0                        84.37                85.17   
C               1.0                       181.91               196.36   
                3.0                       219.82               176.00   

START_TIME                   2016-10-19 06:00:00  2016-10-19 06:20:00  \
intersection_id tollgate_id                                             
A               2.0                        40.01                57.01   
                3.0                        89.51               161.63   
B               1.0                       111.04               111.04   
                3.0                       102.83               106.34   
C               1.0                       196.36    

In [562]:
TEST_DF = pd.DataFrame()
for TRN_STA_M,TRN_END_M,TRN_STA_A,TRN_END_A in test_date_list:
    TRAIN_M_temp = TEST_FULL_TAB_FILL.loc[:,TRN_STA_M:TRN_END_M] 
    TRAIN_A_temp = TEST_FULL_TAB_FILL.loc[:,TRN_STA_A:TRN_END_A] 
    TRAIN_M_temp.columns = np.arange(TRAIN_M_temp.shape[1])
    TRAIN_A_temp.columns = np.arange(TRAIN_A_temp.shape[1])
    
    TRAIN_M_temp.loc[:,'TRN_STA']  = str(TRN_STA_M)
    TRAIN_M_temp.loc[:,'TRN_END'] = str(TRN_END_M)    
    
    TRAIN_A_temp.loc[:,'TRN_STA']  = str(TRN_STA_A)
    TRAIN_A_temp.loc[:,'TRN_END'] = str(TRN_END_A)    
     
    TRAIN_M_temp.reset_index(level=0, inplace=True)
    TRAIN_A_temp.reset_index(level=0, inplace=True)
    
    TEST_DF = pd.concat( [TEST_DF,TRAIN_M_temp],) 
    TEST_DF = pd.concat( [TEST_DF,TRAIN_A_temp],) 
TEST_DF.reset_index(level=0, inplace=True)    

f:\python35\lib\site-packages\pandas\core\indexing.py:297: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self.obj[key] = _infer_fill_value(value)
f:\python35\lib\site-packages\pandas\core\indexing.py:477: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self.obj[item] = s


In [563]:
TEST_DF

tollgate_id intersection_id       0       1       2       3       4  \
0           2.0               A   41.10   43.68   68.02   52.61   56.17   
1           3.0               A   69.48  142.01  233.68  143.65  151.51   
2           1.0               B   57.82   48.68  112.52   97.32   97.32   
3           3.0               B   54.75  121.02   94.04  120.60   73.40   
4           1.0               C  145.35  136.22  147.82  180.98  136.51   
5           3.0               C  139.53  139.53  104.42  182.06  182.06   
6           2.0               A   99.96   88.36   74.89   63.30   71.36   
7           3.0               A  133.05  121.57  147.37  117.07  134.27   
8           1.0               B  142.75  108.19   90.01  101.62  150.39   
9           3.0               B  135.06   61.22  132.87  111.90   84.37   
10          1.0               C  168.90  218.69  178.16  158.96  181.91   
11          3.0               C  164.61  146.60  174.84  171.98  219.82   
12          2.0               A   40.01   57.01   37.41   69.58  100.11   
13          3.0               A   89.51  161.63  133.43  139.88  171.77   
14          1.0               B  111.04  111.04   85.23  209.86  120.88   
15          3.0               B  102.83  106.34  106.34  141.43   73.72   
16          1.0               C  196.36  196.36  196.36  147.55  128.38   
17          3.0               C  126.74  126.74  126.74  126.74   98.03   
18          2.0               A   64.46   62.31   57.33   67.58   55.19   
19          3.0               A  110.05  115.01  132.10   93.67  122.82   
20          1.0               B  183.48  149.28  117.02  153.49  131.38   
21          3.0               B   82.13  128.95   84.24  115.72  141.25   
22          1.0               C  246.94  202.37  204.09  275.37  171.05   
23          3.0               C  275.57  150.17  188.24  166.07  155.71   
24          2.0               A   63.58   49.79   60.88   74.07   62.99   
25          3.0               A  113.05  101.67  201.20  160.84  143.93   
26          1.0               B   70.72   70.72  121.42  106.16  111.77   
27          3.0               B  126.27   84.63  110.79  110.79   66.86   
28          1.0               C  181.54  157.32  162.36  247.70  247.70   
29          3.0               C  157.02  157.02  157.02   92.89  717.25   
..          ...             ...     ...     ...     ...     ...     ...   
54          2.0               A   63.87   68.15   58.80   68.98   82.07   
55          3.0               A  138.25  106.31  104.53  127.06  123.79   
56          1.0               B  137.71  143.04  156.38  123.61  116.61   
57          3.0               B  105.32   81.86  122.33   98.95   95.10   
58          1.0               C  187.74  184.88  245.56  222.29  178.02   
59          3.0               C  169.53  256.40  294.56  223.71  170.00   
60          2.0               A   65.99   68.98   77.07   43.38   49.54   
61          3.0               A   92.97   81.58  116.61   85.37   81.70   
62          1.0               B   84.29  152.89  167.50  106.93  106.93   
63          3.0               B  124.97  100.63  100.63   87.34  102.72   
64          1.0               C  207.94  207.94  219.97  124.00  127.91   
65          3.0               C  121.43  121.43  121.43  211.32  142.34   
66          2.0               A   94.77   79.39   92.50   71.31   75.19   
67          3.0               A  130.81  184.17  210.55  136.33   94.69   
68          1.0               B  148.95  116.16  118.40  112.85  143.97   
69          3.0               B  100.44  111.74  106.38  103.15  149.42   
70          1.0               C  160.53  206.22  195.08  176.23  196.48   
71          3.0               C  163.58  151.95  172.49  224.29  197.32   
72          2.0               A   41.19   50.12   37.17   75.68   54.03   
73          3.0               A  106.01  210.16  140.73  172.79  183.16   
74          1.0               B   88.82   88.82  144.24  103.84  103.84   
75          3.0              

In [564]:
TRAIN_TRN_C =  list(map(lambda x:'SA'+ str(x).zfill(2), np.arange(6)))

In [566]:
TEST_DF.columns = ['TOLLGATE_ID','INTERSECTION_ID']  + TRAIN_TRN_C + ['TRN_STA','TRN_END']

In [567]:
TEST_DF

TOLLGATE_ID INTERSECTION_ID    SA00    SA01    SA02    SA03    SA04  \
0           2.0               A   41.10   43.68   68.02   52.61   56.17   
1           3.0               A   69.48  142.01  233.68  143.65  151.51   
2           1.0               B   57.82   48.68  112.52   97.32   97.32   
3           3.0               B   54.75  121.02   94.04  120.60   73.40   
4           1.0               C  145.35  136.22  147.82  180.98  136.51   
5           3.0               C  139.53  139.53  104.42  182.06  182.06   
6           2.0               A   99.96   88.36   74.89   63.30   71.36   
7           3.0               A  133.05  121.57  147.37  117.07  134.27   
8           1.0               B  142.75  108.19   90.01  101.62  150.39   
9           3.0               B  135.06   61.22  132.87  111.90   84.37   
10          1.0               C  168.90  218.69  178.16  158.96  181.91   
11          3.0               C  164.61  146.60  174.84  171.98  219.82   
12          2.0               A   40.01   57.01   37.41   69.58  100.11   
13          3.0               A   89.51  161.63  133.43  139.88  171.77   
14          1.0               B  111.04  111.04   85.23  209.86  120.88   
15          3.0               B  102.83  106.34  106.34  141.43   73.72   
16          1.0               C  196.36  196.36  196.36  147.55  128.38   
17          3.0               C  126.74  126.74  126.74  126.74   98.03   
18          2.0               A   64.46   62.31   57.33   67.58   55.19   
19          3.0               A  110.05  115.01  132.10   93.67  122.82   
20          1.0               B  183.48  149.28  117.02  153.49  131.38   
21          3.0               B   82.13  128.95   84.24  115.72  141.25   
22          1.0               C  246.94  202.37  204.09  275.37  171.05   
23          3.0               C  275.57  150.17  188.24  166.07  155.71   
24          2.0               A   63.58   49.79   60.88   74.07   62.99   
25          3.0               A  113.05  101.67  201.20  160.84  143.93   
26          1.0               B   70.72   70.72  121.42  106.16  111.77   
27          3.0               B  126.27   84.63  110.79  110.79   66.86   
28          1.0               C  181.54  157.32  162.36  247.70  247.70   
29          3.0               C  157.02  157.02  157.02   92.89  717.25   
..          ...             ...     ...     ...     ...     ...     ...   
54          2.0               A   63.87   68.15   58.80   68.98   82.07   
55          3.0               A  138.25  106.31  104.53  127.06  123.79   
56          1.0               B  137.71  143.04  156.38  123.61  116.61   
57          3.0               B  105.32   81.86  122.33   98.95   95.10   
58          1.0               C  187.74  184.88  245.56  222.29  178.02   
59          3.0               C  169.53  256.40  294.56  223.71  170.00   
60          2.0               A   65.99   68.98   77.07   43.38   49.54   
61          3.0               A   92.97   81.58  116.61   85.37   81.70   
62          1.0               B   84.29  152.89  167.50  106.93  106.93   
63          3.0               B  124.97  100.63  100.63   87.34  102.72   
64          1.0               C  207.94  207.94  219.97  124.00  127.91   
65          3.0               C  121.43  121.43  121.43  211.32  142.34   
66          2.0               A   94.77   79.39   92.50   71.31   75.19   
67          3.0               A  130.81  184.17  210.55  136.33   94.69   
68          1.0               B  148.95  116.16  118.40  112.85  143.97   
69          3.0               B  100.44  111.74  106.38  103.15  149.42   
70          1.0               C  160.53  206.22  195.08  176.23  196.48   
71          3.0               C  163.58  151.95  172.49  224.29  197.32   
72          2.0               A   41.19   50.12   37.17   75.68   54.03   
73          3.0               A  106.01  210.16  140.73  172.79  183.16   
74          1.0               B   88.82   88.82  144.24  103.84  103.84   
75          3.0              

In [570]:
TEST_DF.to_csv("TEST_DF.csv",index=None,encoding='utf-8')

In [571]:
###############MERGE ALL FEATURE ###########################

In [578]:
TEST_DF['TOLLGATE_ID'] = TEST_DF['TOLLGATE_ID'].apply(lambda x:int(x))

In [579]:
TEST_DF

TOLLGATE_ID INTERSECTION_ID    SA00    SA01    SA02    SA03    SA04  \
0             2               A   41.10   43.68   68.02   52.61   56.17   
1             3               A   69.48  142.01  233.68  143.65  151.51   
2             1               B   57.82   48.68  112.52   97.32   97.32   
3             3               B   54.75  121.02   94.04  120.60   73.40   
4             1               C  145.35  136.22  147.82  180.98  136.51   
5             3               C  139.53  139.53  104.42  182.06  182.06   
6             2               A   99.96   88.36   74.89   63.30   71.36   
7             3               A  133.05  121.57  147.37  117.07  134.27   
8             1               B  142.75  108.19   90.01  101.62  150.39   
9             3               B  135.06   61.22  132.87  111.90   84.37   
10            1               C  168.90  218.69  178.16  158.96  181.91   
11            3               C  164.61  146.60  174.84  171.98  219.82   
12            2               A   40.01   57.01   37.41   69.58  100.11   
13            3               A   89.51  161.63  133.43  139.88  171.77   
14            1               B  111.04  111.04   85.23  209.86  120.88   
15            3               B  102.83  106.34  106.34  141.43   73.72   
16            1               C  196.36  196.36  196.36  147.55  128.38   
17            3               C  126.74  126.74  126.74  126.74   98.03   
18            2               A   64.46   62.31   57.33   67.58   55.19   
19            3               A  110.05  115.01  132.10   93.67  122.82   
20            1               B  183.48  149.28  117.02  153.49  131.38   
21            3               B   82.13  128.95   84.24  115.72  141.25   
22            1               C  246.94  202.37  204.09  275.37  171.05   
23            3               C  275.57  150.17  188.24  166.07  155.71   
24            2               A   63.58   49.79   60.88   74.07   62.99   
25            3               A  113.05  101.67  201.20  160.84  143.93   
26            1               B   70.72   70.72  121.42  106.16  111.77   
27            3               B  126.27   84.63  110.79  110.79   66.86   
28            1               C  181.54  157.32  162.36  247.70  247.70   
29            3               C  157.02  157.02  157.02   92.89  717.25   
..          ...             ...     ...     ...     ...     ...     ...   
54            2               A   63.87   68.15   58.80   68.98   82.07   
55            3               A  138.25  106.31  104.53  127.06  123.79   
56            1               B  137.71  143.04  156.38  123.61  116.61   
57            3               B  105.32   81.86  122.33   98.95   95.10   
58            1               C  187.74  184.88  245.56  222.29  178.02   
59            3               C  169.53  256.40  294.56  223.71  170.00   
60            2               A   65.99   68.98   77.07   43.38   49.54   
61            3               A   92.97   81.58  116.61   85.37   81.70   
62            1               B   84.29  152.89  167.50  106.93  106.93   
63            3               B  124.97  100.63  100.63   87.34  102.72   
64            1               C  207.94  207.94  219.97  124.00  127.91   
65            3               C  121.43  121.43  121.43  211.32  142.34   
66            2               A   94.77   79.39   92.50   71.31   75.19   
67            3               A  130.81  184.17  210.55  136.33   94.69   
68            1               B  148.95  116.16  118.40  112.85  143.97   
69            3               B  100.44  111.74  106.38  103.15  149.42   
70            1               C  160.53  206.22  195.08  176.23  196.48   
71            3               C  163.58  151.95  172.49  224.29  197.32   
72            2               A   41.19   50.12   37.17   75.68   54.03   
73            3               A  106.01  210.16  140.73  172.79  183.16   
74            1               B   88.82   88.82  144.24  103.84  103.84   
75            3              

In [583]:
TRAIN_OK['TOLLGATE_ID'] = TRAIN_OK['TOLLGATE_ID'].apply(lambda x:int(x))

f:\python35\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.


In [584]:
TRAIN_OK

TOLLGATE_ID INTERSECTION_ID    SA00    SA01    SA02    SA03    SA04  \
60               2               A   41.92   39.43   48.13   62.11   46.12   
66               2               A   39.43   48.13   62.11   46.12   49.56   
72               2               A   48.13   62.11   46.12   49.56   54.84   
78               2               A   62.11   46.12   49.56   54.84   58.08   
84               2               A   46.12   49.56   54.84   58.08   46.36   
90               2               A   49.56   54.84   58.08   46.36   48.59   
96               2               A   54.84   58.08   46.36   48.59   66.64   
102              2               A   58.08   46.36   48.59   66.64   64.68   
108              2               A   46.36   48.59   66.64   64.68   85.68   
109              3               A  124.66   89.85  180.02  101.39  124.29   
111              3               B  145.94  127.35   97.20  118.43   82.63   
114              2               A   48.59   66.64   64.68   85.68   58.97   
115              3               A   89.85  180.02  101.39  124.29  155.49   
117              3               B  127.35   97.20  118.43   82.63  110.50   
120              2               A   66.64   64.68   85.68   58.97   81.60   
121              3               A  180.02  101.39  124.29  155.49  137.38   
123              3               B   97.20  118.43   82.63  110.50  125.76   
126              2               A   64.68   85.68   58.97   81.60   80.21   
127              3               A  101.39  124.29  155.49  137.38  165.48   
129              3               B  118.43   82.63  110.50  125.76  141.33   
132              2               A   85.68   58.97   81.60   80.21   63.45   
133              3               A  124.29  155.49  137.38  165.48  136.68   
135              3               B   82.63  110.50  125.76  141.33  176.08   
138              2               A   58.97   81.60   80.21   63.45   78.05   
139              3               A  155.49  137.38  165.48  136.68  192.68   
141              3               B  110.50  125.76  141.33  176.08  165.29   
144              2               A   81.60   80.21   63.45   78.05   69.04   
145              3               A  137.38  165.48  136.68  192.68  159.78   
147              3               B  125.76  141.33  176.08  165.29  127.38   
150              2               A   80.21   63.45   78.05   69.04   69.66   
...            ...             ...     ...     ...     ...     ...     ...   
39156            2               A   90.64   71.70   53.86   69.77   61.90   
39157            3               A  117.88  131.03  109.92  111.73  118.20   
39162            2               A   71.70   53.86   69.77   61.90   76.76   
39163            3               A  131.03  109.92  111.73  118.20  125.57   
39168            2               A   53.86   69.77   61.90   76.76   58.04   
39169            3               A  109.92  111.73  118.20  125.57  152.19   
39174            2               A   69.77   61.90   76.76   58.04   53.69   
39175            3               A  111.73  118.20  125.57  152.19  125.55   
39180            2               A   61.90   76.76   58.04   53.69   65.40   
39181            3               A  118.20  125.57  152.19  125.55  158.01   
39186            2               A   76.76   58.04   53.69   65.40   48.66   
39187            3               A  125.57  152.19  125.55  158.01  115.05   
39192            2               A   58.04   53.69   65.40   48.66   60.41   
39193            3               A  152.19  125.55  158.01  115.05  116.37   
39198            2               A   53.69   65.40   48.66   60.41   85.12   
39199            3               A  125.55  158.01  115.05  116.37  107.77   
39204            2               A   65.40   48.66   60.41   85.12   67.14   
39205            3               A  158.01  115.05  116.37  107.77  131.23   
39210            2               A   48.66   60.41   85.12   67.14   65.93   
39211            3           

In [574]:
ROUTES_FEATURES = pd.read_csv('ROUTES_FEATURES.csv')

In [575]:
ROUTES_FEATURES

INTERSECTION_ID  TOLLGATE_ID  SUM_LENGTH      SI00      SI01      SI02  \
0               A            2         384  1.066318  1.032036  0.986718   
1               A            3         852  1.087759  1.034343  1.005512   
2               B            1         821  1.029009  1.053367  0.951372   
3               B            3         477  1.028491  1.004573  0.990055   
4               C            1        1550  1.013151  1.088654  0.940862   
5               C            3        1206  1.014416  1.051595  0.952299   

       SI03      SI04      SI05      SI06      SI07      SI08         FIX  \
0  0.979656  0.974681  0.973236  1.027403  1.005816  0.954137   62.307596   
1  0.973204  1.004882  0.965104  0.986073  0.977839  0.965284  111.117531   
2  0.981350  0.967933  0.953846  1.019755  1.031411  1.011957  119.254085   
3  0.968959  1.005461  0.993016  0.993710  1.024939  0.990796  108.074765   
4  0.961804  0.998508  0.939183  1.003374  1.036067  1.018397  175.727126   
5  0.977064  0.983878  0.950471  0.988199  1.066288  1.015789  180.499997   

      RATIO  ROUTE_HOUR_head  ROUTE_PCT_head  ROUTE_MIN_TTIME  \
0  1.033218                8        0.057396         0.109890   
1  1.051643                9        0.066814         0.175824   
2  0.976876               14        0.068080         1.967033   
3  1.023810                9        0.060641         0.428571   
4  0.930646               13        0.064293         1.802198   
5  0.964646               16        0.079021         3.219780   

   ROUTE_MAX_TTIME  ROUTE_LAST_TTIME  ROUTE_MEAN_TTIME  
0        23.000000         22.890110         12.128412  
1        22.934066         22.758242         12.511789  
2        22.010989         20.043956         12.681418  
3        22.758242         22.329670         12.755572  
4        22.054945         20.252747         13.084869  
5        21.978022         18.758242         13.524524

In [587]:
TRAIN_OK_ROUTES = pd.merge(TRAIN_OK,ROUTES_FEATURES,on=['INTERSECTION_ID','TOLLGATE_ID'],how='left')

In [589]:
TEST_DF_ROUTES = pd.merge(TEST_DF,ROUTES_FEATURES,on=['INTERSECTION_ID','TOLLGATE_ID'],how='left')

In [593]:
ALL_FEATURE_LIST = ['TOLLGATE_ID','INTERSECTION_ID','SA00','SA01','SA02','SA03','SA04','SA05','TRN_STA','TRN_END','SUM_LENGTH'
                    ,'SI00','SI01','SI02','SI03','SI04','SI05','SI06','SI07','SI08','FIX','RATIO','ROUTE_HOUR_head'
                    ,'ROUTE_PCT_head','ROUTE_MIN_TTIME','ROUTE_MAX_TTIME','ROUTE_LAST_TTIME','ROUTE_MEAN_TTIME']
TRAIN_TST_C = ['SB00', 'SB01', 'SB02', 'SB03', 'SB04', 'SB05']
X = TRAIN_OK_ROUTES[ALL_FEATURE_LIST]
Y = TRAIN_OK_ROUTES[TRAIN_TST_C]
X_test = TEST_DF_ROUTES[ALL_FEATURE_LIST]

In [594]:
X.to_csv('X.csv', index = False)
Y.to_csv('Y.csv', index = False)
X_test.to_csv('Xtest.csv', index = False)

In [36]:
# ADD WEATHER FEATURE

In [40]:
X = pd.read_csv('X.csv')
Y = pd.read_csv('Y.csv')
Xtest = pd.read_csv('Xtest.csv')
TRAIN_WEATHER_UPDATE_FULL = pd.read_csv('TRAIN_WEATHER_UPDATE_FULL.csv')
TEST_WEATHER_FULL = pd.read_csv('TEST_WEATHER_FULL.csv')

In [42]:
TRAIN_WEATHER_UPDATE_FULL['concrete_date']=pd.to_datetime(TRAIN_WEATHER_UPDATE_FULL['concrete_date'])
TRAIN_WEATHER_UPDATE_FULL_TAB = pd.pivot_table(TRAIN_WEATHER_UPDATE_FULL, values=['pressure','sea_pressure','wind_direction','precipitation','SSD'],index=['concrete_date'])
TEST_WEATHER_FULL['concrete_date']=pd.to_datetime(TEST_WEATHER_FULL['concrete_date'])
TEST_WEATHER_FULL_TAB = pd.pivot_table(TEST_WEATHER_FULL, values=['pressure','sea_pressure','wind_direction','precipitation','SSD'],index=['concrete_date'])

In [43]:
X['TST_STA']=X['TRN_END'].apply(lambda x:datetime.datetime.strptime(x,'%Y-%m-%d %H:%M:%S')+ datetime.timedelta(minutes=20))
X['XTST_END']=X['TRN_END'].apply(lambda x:datetime.datetime.strptime(x,'%Y-%m-%d %H:%M:%S')+ datetime.timedelta(hours=2))
Xtest['TST_STA']=Xtest['TRN_END'].apply(lambda x:datetime.datetime.strptime(x,'%Y-%m-%d %H:%M:%S')+ datetime.timedelta(minutes=20))
Xtest['XTST_END']=Xtest['TRN_END'].apply(lambda x:datetime.datetime.strptime(x,'%Y-%m-%d %H:%M:%S')+ datetime.timedelta(hours=2))

In [44]:
TRN_WEATHER = pd.DataFrame()
TST_WEATHER = pd.DataFrame()
for x in range(X.shape[0]):
    each_row = X.iloc[x]
    TRN_weather = TRAIN_WEATHER_UPDATE_FULL_TAB.loc[each_row['TRN_STA']:each_row['TRN_END']]
    TRN_WEATHER = pd.concat([TRN_WEATHER,pd.DataFrame(TRN_weather.mean()).T],axis=0)
    TST_weather = TRAIN_WEATHER_UPDATE_FULL_TAB.loc[each_row['TST_STA']:each_row['XTST_END']]
    TST_WEATHER = pd.concat([TST_WEATHER,pd.DataFrame(TST_weather.mean()).T],axis=0)
TRN_WEATHER.columns = [(lambda x:('TRNW'+ str(x).zfill(2))) (x)  for x in range(TRN_WEATHER.shape[1])]
TST_WEATHER.columns = [(lambda x:('TSTW'+ str(x).zfill(2))) (x)  for x in range(TST_WEATHER.shape[1])]
W= pd.concat([TST_WEATHER,TRN_WEATHER],axis=1)
W.reset_index(drop=True,inplace=True)
X_F = pd.concat([X,W],axis=1)

In [50]:
X

TOLLGATE_ID INTERSECTION_ID    SA00    SA01    SA02    SA03    SA04  \
0                2               A   41.92   39.43   48.13   62.11   46.12   
1                2               A   39.43   48.13   62.11   46.12   49.56   
2                2               A   48.13   62.11   46.12   49.56   54.84   
3                2               A   62.11   46.12   49.56   54.84   58.08   
4                2               A   46.12   49.56   54.84   58.08   46.36   
5                2               A   49.56   54.84   58.08   46.36   48.59   
6                2               A   54.84   58.08   46.36   48.59   66.64   
7                2               A   58.08   46.36   48.59   66.64   64.68   
8                2               A   46.36   48.59   66.64   64.68   85.68   
9                3               A  124.66   89.85  180.02  101.39  124.29   
10               3               B  145.94  127.35   97.20  118.43   82.63   
11               2               A   48.59   66.64   64.68   85.68   58.97   
12               3               A   89.85  180.02  101.39  124.29  155.49   
13               3               B  127.35   97.20  118.43   82.63  110.50   
14               2               A   66.64   64.68   85.68   58.97   81.60   
15               3               A  180.02  101.39  124.29  155.49  137.38   
16               3               B   97.20  118.43   82.63  110.50  125.76   
17               2               A   64.68   85.68   58.97   81.60   80.21   
18               3               A  101.39  124.29  155.49  137.38  165.48   
19               3               B  118.43   82.63  110.50  125.76  141.33   
20               2               A   85.68   58.97   81.60   80.21   63.45   
21               3               A  124.29  155.49  137.38  165.48  136.68   
22               3               B   82.63  110.50  125.76  141.33  176.08   
23               2               A   58.97   81.60   80.21   63.45   78.05   
24               3               A  155.49  137.38  165.48  136.68  192.68   
25               3               B  110.50  125.76  141.33  176.08  165.29   
26               2               A   81.60   80.21   63.45   78.05   69.04   
27               3               A  137.38  165.48  136.68  192.68  159.78   
28               3               B  125.76  141.33  176.08  165.29  127.38   
29               2               A   80.21   63.45   78.05   69.04   69.66   
...            ...             ...     ...     ...     ...     ...     ...   
10346            2               A   90.64   71.70   53.86   69.77   61.90   
10347            3               A  117.88  131.03  109.92  111.73  118.20   
10348            2               A   71.70   53.86   69.77   61.90   76.76   
10349            3               A  131.03  109.92  111.73  118.20  125.57   
10350            2               A   53.86   69.77   61.90   76.76   58.04   
10351            3               A  109.92  111.73  118.20  125.57  152.19   
10352            2               A   69.77   61.90   76.76   58.04   53.69   
10353            3               A  111.73  118.20  125.57  152.19  125.55   
10354            2               A   61.90   76.76   58.04   53.69   65.40   
10355            3               A  118.20  125.57  152.19  125.55  158.01   
10356            2               A   76.76   58.04   53.69   65.40   48.66   
10357            3               A  125.57  152.19  125.55  158.01  115.05   
10358            2               A   58.04   53.69   65.40   48.66   60.41   
10359            3               A  152.19  125.55  158.01  115.05  116.37   
10360            2               A   53.69   65.40   48.66   60.41   85.12   
10361            3               A  125.55  158.01  115.05  116.37  107.77   
10362            2               A   65.40   48.66   60.41   85.12   67.14   
10363            3               A  158.01  115.05  116.37  107.77  131.23   
10364            2               A   48.66   60.41   85.12   67.14   65.93   
10365            3           

In [51]:
TRN_WEATHER = pd.DataFrame()
TST_WEATHER = pd.DataFrame()
for x in range(Xtest.shape[0]):
    each_row = Xtest.iloc[x]
    TRN_weather = TEST_WEATHER_FULL_TAB.loc[each_row['TRN_STA']:each_row['TRN_END']]
    TRN_WEATHER = pd.concat([TRN_WEATHER,pd.DataFrame(TRN_weather.mean()).T],axis=0)
    TST_weather = TEST_WEATHER_FULL_TAB.loc[each_row['TST_STA']:each_row['XTST_END']]
    TST_WEATHER = pd.concat([TST_WEATHER,pd.DataFrame(TST_weather.mean()).T],axis=0)
TRN_WEATHER.columns = [(lambda x:('TRNW'+ str(x).zfill(2))) (x)  for x in range(TRN_WEATHER.shape[1])]
TST_WEATHER.columns = [(lambda x:('TSTW'+ str(x).zfill(2))) (x)  for x in range(TST_WEATHER.shape[1])]
W= pd.concat([TST_WEATHER,TRN_WEATHER],axis=1)
W.reset_index(drop=True,inplace=True)
Xtest_F = pd.concat([Xtest,W],axis=1)

In [52]:
Xtest_F

TOLLGATE_ID INTERSECTION_ID    SA00    SA01    SA02    SA03    SA04  \
0             2               A   41.10   43.68   68.02   52.61   56.17   
1             3               A   69.48  142.01  233.68  143.65  151.51   
2             1               B   57.82   48.68  112.52   97.32   97.32   
3             3               B   54.75  121.02   94.04  120.60   73.40   
4             1               C  145.35  136.22  147.82  180.98  136.51   
5             3               C  139.53  139.53  104.42  182.06  182.06   
6             2               A   99.96   88.36   74.89   63.30   71.36   
7             3               A  133.05  121.57  147.37  117.07  134.27   
8             1               B  142.75  108.19   90.01  101.62  150.39   
9             3               B  135.06   61.22  132.87  111.90   84.37   
10            1               C  168.90  218.69  178.16  158.96  181.91   
11            3               C  164.61  146.60  174.84  171.98  219.82   
12            2               A   40.01   57.01   37.41   69.58  100.11   
13            3               A   89.51  161.63  133.43  139.88  171.77   
14            1               B  111.04  111.04   85.23  209.86  120.88   
15            3               B  102.83  106.34  106.34  141.43   73.72   
16            1               C  196.36  196.36  196.36  147.55  128.38   
17            3               C  126.74  126.74  126.74  126.74   98.03   
18            2               A   64.46   62.31   57.33   67.58   55.19   
19            3               A  110.05  115.01  132.10   93.67  122.82   
20            1               B  183.48  149.28  117.02  153.49  131.38   
21            3               B   82.13  128.95   84.24  115.72  141.25   
22            1               C  246.94  202.37  204.09  275.37  171.05   
23            3               C  275.57  150.17  188.24  166.07  155.71   
24            2               A   63.58   49.79   60.88   74.07   62.99   
25            3               A  113.05  101.67  201.20  160.84  143.93   
26            1               B   70.72   70.72  121.42  106.16  111.77   
27            3               B  126.27   84.63  110.79  110.79   66.86   
28            1               C  181.54  157.32  162.36  247.70  247.70   
29            3               C  157.02  157.02  157.02   92.89  717.25   
..          ...             ...     ...     ...     ...     ...     ...   
54            2               A   63.87   68.15   58.80   68.98   82.07   
55            3               A  138.25  106.31  104.53  127.06  123.79   
56            1               B  137.71  143.04  156.38  123.61  116.61   
57            3               B  105.32   81.86  122.33   98.95   95.10   
58            1               C  187.74  184.88  245.56  222.29  178.02   
59            3               C  169.53  256.40  294.56  223.71  170.00   
60            2               A   65.99   68.98   77.07   43.38   49.54   
61            3               A   92.97   81.58  116.61   85.37   81.70   
62            1               B   84.29  152.89  167.50  106.93  106.93   
63            3               B  124.97  100.63  100.63   87.34  102.72   
64            1               C  207.94  207.94  219.97  124.00  127.91   
65            3               C  121.43  121.43  121.43  211.32  142.34   
66            2               A   94.77   79.39   92.50   71.31   75.19   
67            3               A  130.81  184.17  210.55  136.33   94.69   
68            1               B  148.95  116.16  118.40  112.85  143.97   
69            3               B  100.44  111.74  106.38  103.15  149.42   
70            1               C  160.53  206.22  195.08  176.23  196.48   
71            3               C  163.58  151.95  172.49  224.29  197.32   
72            2               A   41.19   50.12   37.17   75.68   54.03   
73            3               A  106.01  210.16  140.73  172.79  183.16   
74            1               B   88.82   88.82  144.24  103.84  103.84   
75            3              